# Dataset generation step by step

In [1]:
!pip install Pillow

In [5]:
from sklearn.metrics import accuracy_score
from sklearn.model_selection import StratifiedShuffleSplit

from livelossplot import PlotLosses
from pycm import *

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import TensorDataset, DataLoader
import torchvision.transforms as transforms
from torchvision.datasets import MNIST
import numpy as np
import random
from PIL import Image
Image.MAX_IMAGE_PIXELS = None
import cv2
from matplotlib.patches import Ellipse,Rectangle

import pylab as plt
import numpy as np
import math
import pandas as pd
import os


In [6]:
df = pd.read_csv("Catalog_Mars_Release_2020_1kmPlus_FullMorphData.csv",engine='python',delimiter=',')
df

CRATER_ID  LAT_CIRC_IMG  LON_CIRC_IMG  LAT_ELLI_IMG  LON_ELLI_IMG  \
0       01-1-000003     79.257599    211.909949     79.257584    211.910021   
1       01-1-000004     78.696512    207.162344     78.696517    207.162105   
2       01-1-000012     77.791422    186.586023     77.791443    186.585690   
3       01-1-000013     76.655040    194.807812     76.655020    194.807973   
4       01-1-000014     76.976285    195.615795     76.976294    195.616254   
...             ...           ...           ...           ...           ...   
392426  16-4-007160    -51.253765     93.980015    -51.253710     93.980005   
392427  16-4-007161    -52.010160    131.870216    -52.010131    131.870172   
392428  16-4-007162    -55.929621    165.240464    -55.929621    165.240425   
392429  16-4-007163    -57.577402    150.020821    -57.577196    150.021399   
392430  16-4-007164    -63.860255    128.517834    -63.860265    128.517791   

        DIAM_CIRC_IMG  DIAM_CIRC_SD_IMG  DIAM_ELLI_MAJOR_IMG  \
0           19.526698          0.230187            19.746718   
1            4.232291          0.089167             4.449180   
2            8.542042          0.193030             8.818632   
3            7.967843          0.139290             8.268589   
4           20.948878          0.340399            21.550893   
...               ...               ...                  ...   
392426       1.325088          0.016568             1.365264   
392427       1.266052          0.014247             1.289768   
392428       1.093010          0.033980             1.144802   
392429       1.765619          0.029925             1.866267   
392430       1.050987          0.031312             1.101924   

        DIAM_ELLI_MINOR_IMG  DIAM_ELLI_ECCEN_IMG  ...  INT_MORPH1  INT_MORPH2  \
0                 19.286041             0.214742  ...      CpxUnc         NaN   
1                  4.019798             0.428605  ...         NaN         NaN   
2                  8.251528             0.352817  ...       CpxFF         NaN   
3                  7.662693             0.375745  ...       CpxFF         NaN   
4                 20.326902             0.332212  ...       CpxFF         NaN   
...                     ...                  ...  ...         ...         ...   
392426             1.279374             0.349092  ...         NaN         NaN   
392427             1.238597             0.278881  ...         NaN         NaN   
392428             1.035258             0.426872  ...         NaN         NaN   
392429             1.708802             0.402033  ...         NaN         NaN   
392430             0.996221             0.427377  ...         NaN         NaN   

            INT_MORPH3  CONF  NOTES  DEG_RIM  DEG_EJC  DEG_FLR  DEG_LEV_1  \
0       Floor Deposits   NaN    NaN      1.0      1.0      1.0          3   
1       Floor Deposits   NaN    NaN      3.0      2.0      1.0          6   
2                  NaN   NaN    NaN      2.0      2.0      2.0          6   
3                  NaN   NaN    NaN      3.0      2.0      3.0          8   
4       Floor Deposits   NaN    NaN      3.0      2.0      3.0          8   
...                ...   ...    ...      ...      ...      ...        ...   
392426             NaN   NaN    NaN      NaN      NaN      NaN          0   
392427             NaN   NaN    NaN      NaN      NaN      NaN          0   
392428             NaN   NaN    NaN      NaN      NaN      NaN          0   
392429             NaN   NaN    NaN      NaN      NaN      NaN          0   
392430             NaN   NaN    NaN      NaN      NaN      NaN          0   

        DEG_LEV  
0             3  
1             6  
2             6  
3             8  
4             8  
...         ...  
392426       -1  
392427       -1  
392428       -1  
392429       -1  
392430       -1  

[392431 rows x 36 columns]

## Search for latitude and longtidude range of the image from csv file

In [7]:
def generate_data(max_lat,min_lat,max_long,min_long,pathsave,df,target_size,im_name,name):
    
    if os.path.exists(pathsave+'/labels') == False:
        os.mkdir(pathsave+'/labels')
    if os.path.exists(pathsave+'/images') == False:
        os.mkdir(pathsave+'/images')
    
    images_path = pathsave+'/images'
    labels_path = pathsave+'/labels'
    df1 = df[(df['LAT_CIRC_IMG']>min_lat) & (df['LAT_CIRC_IMG']<max_lat)]
    df1 = df1[df1['LON_CIRC_IMG']>min_long]
    df1 = df1[df1['LON_CIRC_IMG']<max_long]

    df2 = df1.copy()
    df2['x'] = 1
    df2['y'] = 1
    df2['w'] = 1
    df2['h'] = 1
    df2['r']  = 1

    x = df1['LON_ELLI_IMG']
    y = df1['LAT_ELLI_IMG']
    r = df1['DIAM_ELLI_MAJOR_IMG']/2
    lon_ratio = 3378.4*np.cos(math.pi/180*y)*math.pi/180
    lat_ratio = np.pi*3389.5/180
    df2['x'] = x - r/lon_ratio
    df2['y'] = y - r/lat_ratio
    df2['w'] = 2*r/lon_ratio
    df2['h'] = 2*r/lat_ratio
    df2['r'] = r

    img = plt.imread(im_name)
    x = img.shape[1]
    y = img.shape[0]
    df3 = df2.copy()

    df3['x'] = x / (max_long - min_long) * (df2['x'] - min_long)
    df3['y'] = y - y / (max_lat-min_lat) * (df2['y'] - min_lat)
    df3['w'] = x / (max_long-min_long) * df2['w']
    df3['h'] = y / (max_lat-min_lat) * df2['h']


    h, w = img.shape
    c=0
    # x - h, y - w
    crop_size = target_size
    num_y = int(math.floor(h / target_size))
    num_x = int(math.floor(w / target_size))
    print(f"width: {w}, height: {h}, crop size: {crop_size}")
    print(f"num in x direction: {num_x}, num in y direction: {num_y}")

#     images_path = r"C:\Users\jamil\OneDrive\desktop\PhD\master_fyp\dataset_generation_old\menomia\images\*.jpg"
#     labels_path = r"C:\Users\jamil\OneDrive\desktop\PhD\master_fyp\dataset_generation_old\menomia\labels\*.txt"
    clean_images = f'del {images_path}'
    clean_labels = f'del {labels_path}'
    !{clean_images}
    !{clean_labels}

    for i in range(num_y):
        for j in range(num_x):
            x_low = j * crop_size
            y_low = i * crop_size
            x_high = (j + 1) * crop_size
            y_high = (i + 1) * crop_size
            curr_list = []
            offset = 0
            df5 = df3.copy()
            img_crop = img[y_low:y_high, x_low:x_high]
            base_name_img = images_path+'/'+name+'_'+str(i)+'_'+str(j)+'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            base_name_label = labels_path+'/'+name+'_'+str(i)+'_'+str(j)+'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            cv2.imwrite(base_name_img+'.jpg',img_crop)
#             with Image.open(base_name_img+'.jpg') as img:
#                     # Resize the image
#                     resized_img = img.resize(1024, Image.ANTIALIAS)
#                     resized_img.save(output_path)
                            
            df5 = df3[(df3['y']>=y_low-offset) & (df3['y']<=y_high+offset)]
#             if i == 2 and j == 20:
#                 print('filter by y ', df5)
            df5 = df5[(df5['x']>=x_low-offset) & (df5['x']<=x_high+offset)]
#             if i == 2 and j == 20:
#                 print('filter by y and x', df5)
    #         print('len',len(df5))


            if len(df5) == 0:
    #             fileObject = open(''+str(c)+'.txt','a')
                pass
            else:
                x_crop = img_crop.shape[1]
                y_crop = img_crop.shape[0]

                for k in range(len(df5)):
                    y = float(df1['LAT_ELLI_IMG'][df1['LAT_ELLI_IMG'].index[i]])
                    lon_ratio = 3378.4*math.cos(math.pi/180*y)*math.pi/180
                    lat_ratio = math.pi*3389.5/180

                    if df5['h'][df5['h'].index[k]]>60:

                        X = (df5['x'][df5['x'].index[k]]-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
                        Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
                        W = df5['w'][df5['w'].index[k]]/x_crop
                        H = df5['h'][df5['h'].index[k]]/y_crop
                        curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                    elif 20<=df5['h'][df5['h'].index[k]]<=60:
                        X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
                        Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
                        W = df5['w'][df5['w'].index[k]]/x_crop
                        H = df5['h'][df5['h'].index[k]]/y_crop
                        curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                    elif df5['h'][df5['h'].index[k]]<20:
                        X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
                        Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
                        W = df5['w'][df5['w'].index[k]]/x_crop
                        H = df5['h'][df5['h'].index[k]]/y_crop
                        curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

#                     X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*1.8- x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                     Y = (df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]-y_low)/y_crop+df5['h'][df5['h'].index[k]]/x_crop/2
#                     W = df5['w'][df5['w'].index[k]]/x_crop
#                     H = df5['h'][df5['h'].index[k]]/y_crop
#                     curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                with open(base_name_label +'.txt','w') as fileObject:
                    for values in curr_list:
                        for ip in values:
                            fileObject.write(str(ip))
                            fileObject.write(' ')
                        fileObject.write('\n')

            c+=1
            


In [8]:
def generate_data_size(max_lat,min_lat,max_long,min_long,pathsave,df,target_size,im_name,name):
    
    if os.path.exists(pathsave+'/labels') == False:
        os.mkdir(pathsave+'/labels')
    if os.path.exists(pathsave+'/images') == False:
        os.mkdir(pathsave+'/images')
    
    images_path = pathsave+'/images'
    labels_path = pathsave+'/labels'
    df1 = df[(df['LAT_CIRC_IMG']>min_lat) & (df['LAT_CIRC_IMG']<max_lat)]
    df1 = df1[df1['LON_CIRC_IMG']>min_long]
    df1 = df1[df1['LON_CIRC_IMG']<max_long]

    df2 = df1.copy()
    df2['x'] = 1
    df2['y'] = 1
    df2['w'] = 1
    df2['h'] = 1
    df2['r']  = 1

    x = df1['LON_ELLI_IMG']
    y = df1['LAT_ELLI_IMG']
    r = df1['DIAM_ELLI_MAJOR_IMG']/2
    lon_ratio = 3378.4*np.cos(math.pi/180*y)*math.pi/180
    lat_ratio = np.pi*3389.5/180
    df2['x'] = x - r/lon_ratio
    df2['y'] = y - r/lat_ratio
    df2['w'] = 2*r/lon_ratio
    df2['h'] = 2*r/lat_ratio
    df2['r'] = r

    img = plt.imread(im_name)
    x = img.shape[1]
    y = img.shape[0]
    df3 = df2.copy()

    df3['x'] = x / (max_long - min_long) * (df2['x'] - min_long)
    df3['y'] = y - y / (max_lat-min_lat) * (df2['y'] - min_lat)
    df3['w'] = x / (max_long-min_long) * df2['w']
    df3['h'] = y / (max_lat-min_lat) * df2['h']


    h, w = img.shape
    c=0
    # x - h, y - w
    crop_size = target_size
    num_y = int(math.floor(h / target_size))
    num_x = int(math.floor(w / target_size))
    print(f"width: {w}, height: {h}, crop size: {crop_size}")
    print(f"num in x direction: {num_x}, num in y direction: {num_y}")

#     images_path = r"C:\Users\jamil\OneDrive\desktop\PhD\master_fyp\dataset_generation_old\menomia\images\*.jpg"
#     labels_path = r"C:\Users\jamil\OneDrive\desktop\PhD\master_fyp\dataset_generation_old\menomia\labels\*.txt"
    clean_images = f'del {images_path}'
    clean_labels = f'del {labels_path}'
    !{clean_images}
    !{clean_labels}

    for i in range(num_y):
        for j in range(num_x):
            x_low = j * crop_size
            y_low = i * crop_size
            x_high = (j + 1) * crop_size
            y_high = (i + 1) * crop_size
            curr_list = []
            offset = 0
            df5 = df3.copy()
            img_crop = img[y_low:y_high, x_low:x_high]
            base_name_img = images_path+'/'+name+'_'+str(i)+'_'+str(j)+'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            base_name_label = labels_path+'/'+name+'_'+str(i)+'_'+str(j)+'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            cv2.imwrite(base_name_img+'.jpg',img_crop)
#             with Image.open(base_name_img+'.jpg') as img:
#                     # Resize the image
#                     resized_img = img.resize(1024, Image.ANTIALIAS)
#                     resized_img.save(output_path)
                            
            df5 = df3[(df3['y']>=y_low-offset) & (df3['y']<=y_high+offset)]
#             if i == 2 and j == 20:
#                 print('filter by y ', df5)
            df5 = df5[(df5['x']>=x_low-offset) & (df5['x']<=x_high+offset)]
#             if i == 2 and j == 20:
#                 print('filter by y and x', df5)
    #         print('len',len(df5))


            if len(df5) == 0:
    #             fileObject = open(''+str(c)+'.txt','a')
                pass
            else:
                x_crop = img_crop.shape[1]
                y_crop = img_crop.shape[0]

                for k in range(len(df5)):
                    y = float(df1['LAT_ELLI_IMG'][df1['LAT_ELLI_IMG'].index[i]])
                    lon_ratio = 3378.4*math.cos(math.pi/180*y)*math.pi/180
                    lat_ratio = math.pi*3389.5/180

                    if df5['h'][df5['h'].index[k]]>60:

                        X = (df5['x'][df5['x'].index[k]]-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
                        Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
                        W = df5['w'][df5['w'].index[k]]/x_crop
                        H = df5['h'][df5['h'].index[k]]/y_crop
                        curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                    elif 10<=df5['h'][df5['h'].index[k]]<=60:
                        X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
                        Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
                        W = df5['w'][df5['w'].index[k]]/x_crop
                        H = df5['h'][df5['h'].index[k]]/y_crop
                        curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

#                     elif df5['h'][df5['h'].index[k]]<20:
#                         X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                         Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
#                         W = df5['w'][df5['w'].index[k]]/x_crop
#                         H = df5['h'][df5['h'].index[k]]/y_crop
#                         curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                    else:
                        pass

#                     X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*1.8- x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                     Y = (df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]-y_low)/y_crop+df5['h'][df5['h'].index[k]]/x_crop/2
#                     W = df5['w'][df5['w'].index[k]]/x_crop
#                     H = df5['h'][df5['h'].index[k]]/y_crop
#                     curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

                with open(base_name_label +'.txt','w') as fileObject:
                    for values in curr_list:
                        for ip in values:
                            fileObject.write(str(ip))
                            fileObject.write(' ')
                        fileObject.write('\n')

            c+=1
            


In [9]:
def generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,target_size,im_name,name):
    
    if os.path.exists(pathsave+'/labels') == False:
        os.mkdir(pathsave+'/labels')
    if os.path.exists(pathsave+'/images') == False:
        os.mkdir(pathsave+'/images')
    
    images_path = pathsave+'/images'
    labels_path = pathsave+'/labels'
    df1 = df[(df['LAT_CIRC_IMG']>min_lat) & (df['LAT_CIRC_IMG']<max_lat)]
    df1 = df1[df1['LON_CIRC_IMG']>min_long]
    df1 = df1[df1['LON_CIRC_IMG']<max_long]

    df2 = df1.copy()
    df2['x'] = 1
    df2['y'] = 1
    df2['w'] = 1
    df2['h'] = 1
    df2['r']  = 1

    x = df1['LON_ELLI_IMG']
    y = df1['LAT_ELLI_IMG']
    r = df1['DIAM_ELLI_MAJOR_IMG']/2
    lon_ratio = 3378.4*np.cos(math.pi/180*y)*math.pi/180
    lat_ratio = np.pi*3389.5/180
    df2['x'] = x - r/lon_ratio
    df2['y'] = y - r/lat_ratio
    df2['w'] = 2*r/lon_ratio
    df2['h'] = 2*r/lat_ratio
    df2['r'] = r

    img = plt.imread(im_name)
    x = img.shape[1]
    y = img.shape[0]
    df3 = df2.copy()

    df3['x'] = x / (max_long - min_long) * (df2['x'] - min_long)
    df3['y'] = y - y / (max_lat-min_lat) * (df2['y'] - min_lat)
    df3['w'] = x / (max_long-min_long) * df2['w']
    df3['h'] = y / (max_lat-min_lat) * df2['h']


    h, w = img.shape
    c=0
    # x - h, y - w
    crop_size = target_size
    num_y = int(math.floor(h / target_size))
    num_x = int(math.floor(w / target_size))
    print(f"width: {w}, height: {h}, crop size: {crop_size}")
    print(f"num in x direction: {num_x}, num in y direction: {num_y}")


    clean_images = f'del {images_path}'
    clean_labels = f'del {labels_path}'
    !{clean_images}
    !{clean_labels}

    # Calculate initial number of crops horizontally and vertically without overlap
    num_x = ceil(w / crop_size)
    num_y = ceil(h / crop_size)

    # Dynamically calculate overlap based on remaining space for the last crop
    overlap_x = (num_x * crop_size - w) / (num_x - 1) if num_x > 1 else 0
    overlap_y = (num_y * crop_size - h) / (num_y - 1) if num_y > 1 else 0

    for i in tqdm(range(num_y)):
        for j in range(num_x):
            x_low = j * crop_size - j * overlap_x
            y_low = i * crop_size - i * overlap_y

            # Ensure the calculated starting points are within the image boundaries
            x_low, y_low = math.floor(max(0, x_low)), math.floor(max(0, y_low))
            x_high, y_high = x_low + crop_size, y_low + crop_size
            x_high = math.floor(min(x_high, w))
            y_high = math.floor(min(y_high, h))

#             print('crop_size:',x_high-x_low, y_high-y_low)
            
            curr_list = []
            offset = 0
            df5 = df3.copy()
            img_crop = img[y_low:y_high, x_low:x_high]
            base_name_img = images_path+'/'+name+'_'+str(x_low)+'_'+str(y_low)+'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            base_name_label = labels_path+'/'+name+'_'+ str(x_low) +'_'+ str(y_low) +'_'+str(max_lat)+ '_' + str(min_lat)+ '_' + str(max_long)+ '_' + str(min_long)
            cv2.imwrite(base_name_img+'.jpg',img_crop)
#             with Image.open(base_name_img+'.jpg') as img:
#                     # Resize the image
#                     resized_img = img.resize(1024, Image.ANTIALIAS)
#                     resized_img.save(output_path)
                            
#             df5 = df3[(df3['y']>=y_low-offset) & (df3['y']<=y_high+offset)]
#             df5 = df5[(df5['x']>=x_low-offset) & (df5['x']<=x_high+offset)]



#             if len(df5) == 0:
#     #             fileObject = open(''+str(c)+'.txt','a')
#                 pass
#             else:
#                 x_crop = img_crop.shape[1]
#                 y_crop = img_crop.shape[0]

#                 for k in range(len(df5)):
#                     y = float(df1['LAT_ELLI_IMG'][df1['LAT_ELLI_IMG'].index[i]])
#                     lon_ratio = 3378.4*math.cos(math.pi/180*y)*math.pi/180
#                     lat_ratio = math.pi*3389.5/180

#                     if df5['h'][df5['h'].index[k]]>60:

#                         X = (df5['x'][df5['x'].index[k]]-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                         Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
#                         W = df5['w'][df5['w'].index[k]]/x_crop
#                         H = df5['h'][df5['h'].index[k]]/y_crop
#                         curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

#                     elif 10<=df5['h'][df5['h'].index[k]]<=60:
#                         X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                         Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
#                         W = df5['w'][df5['w'].index[k]]/x_crop
#                         H = df5['h'][df5['h'].index[k]]/y_crop
#                         curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

#                     elif 10<=df5['h'][df5['h'].index[k]]<=60:
#                         X = (df5['x'][df5['x'].index[k]]-df5['r'][df5['r'].index[k]]*2-x_low)/x_crop+df5['w'][df5['w'].index[k]]/x_crop/2
#                         Y = ((df5['y'][df5['y'].index[k]]-20*df5['r'][df5['r'].index[k]]- y_low))/y_crop+df5['h'][df5['h'].index[k]]/y_crop/2
#                         W = df5['w'][df5['w'].index[k]]/x_crop
#                         H = df5['h'][df5['h'].index[k]]/y_crop
#                         curr_list.append(['0', max(min(X, 0.99), 0.01), max(min(Y, 0.99), 0.01), max(min(W, 0.99), 0.01), max(min(H, 0.99), 0.01)])

#                     else:
#                         pass

#                 with open(base_name_label +'.txt','w') as fileObject:
#                     for values in curr_list:
#                         for ip in values:
#                             fileObject.write(str(ip))
#                             fileObject.write(' ')
#                         fileObject.write('\n')

            c+=1
            


In [10]:
import os
from PIL import Image

def downsample_image(input_path, output_path, new_size=(416, 416)):
    # Open the image
    with Image.open(input_path) as img:
        # Resize the image
        resized_img = img.resize(new_size, Image.ANTIALIAS)
#         print(f"original size: {img.size}, resized img: {resized_img.size}")
        # Save the resized image
        resized_img.save(output_path)

def downsample_images_in_folder(input_folder, output_folder):
    # Create the output folder if it doesn't exist
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)

    # Iterate over all files in the input folder
    for filename in os.listdir(input_folder):
        if filename.lower().endswith(('.png', '.jpg', '.jpeg', '.bmp', '.tiff', '.gif')):  # add other file formats if needed
            input_path = os.path.join(input_folder, filename)
            output_path = os.path.join(output_folder, filename)

            # Downsample the image
            downsample_image(input_path, output_path)
            print(f"Downsampled '{filename}' and saved to '{output_folder}'")

# # Set the paths for the input and output folders
# input_folder = 'dataset_generation_old/dataset_6144_Aeolis/images/'  # replace with your input folder path
# output_folder = 'dataset_generation_old/detection_img/6144' # replace with your output folder path

# downsample_images_in_folder(input_folder, output_folder)


In [11]:
import random
def random_sample(files_images, files_labels, nd):
    files_images = sorted(files_images)
    files_labels = sorted(files_labels)
#     print(files_images, files_labels)
    n = len(files_labels)
    if nd>n:
        nd=n
        print(nd)
    sample_index = []
    all_index = []
    all_index = range(0, n, 1)
    print(n,nd)
    sample_index = random.sample(all_index, nd)
    
    delete_index = list(set(all_index) - set(sample_index))
#     print(delete_index)
#     os.remove(os.path.join(path_images, files_images[delete_index]))
#     os.remove(os.path.join(path_labels,files_labels[delete_index]))
    for i in delete_index:
        label_to_delete_name = files_labels[i]
        os.remove(os.path.join(path_labels, label_to_delete_name))
        img_to_delete_name = label_to_delete_name.split('txt')[0] + 'jpg'
        os.remove(os.path.join(path_images, img_to_delete_name))
        

#### MareTyrrhenum

In [12]:
size = 416

In [13]:
from math import ceil
from tqdm import tqdm
name = 'MareTyrrhenum'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name

In [4]:
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_MareTyrrhenum_30S090E_100mpp.jpg'
output_path = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

max_lat = 0
min_lat = -30
max_long = 135
min_long = 90
# generate_data(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

NameError: name 'pathsave' is not defined

In [418]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


In [35]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)


C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'MareTyrrhenum_0_0_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_10337_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_10751_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_11164_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_11578_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_11991_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_12405_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_1240_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_0_12818_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhen

Downsampled 'MareTyrrhenum_10257_7856_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_8270_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_827_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_8683_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_9097_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_9510_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10257_9924_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10667_0_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_10667_10337_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/

Downsampled 'MareTyrrhenum_11078_6202_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_6616_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_7029_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_7443_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_7856_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_8270_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_827_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_8683_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11078_9097_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_im

Downsampled 'MareTyrrhenum_11898_2067_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_2481_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_2894_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_3308_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_3721_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_4135_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_413_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_4548_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_11898_4962_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_im

...

Downsampled 'MareTyrrhenum_6975_14472_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_14886_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_15299_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_15713_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_16126_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_16540_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_1654_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_16953_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_6975_17367_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_im

Downsampled 'MareTyrrhenum_7795_12405_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_1240_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_12818_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_13232_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_13645_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_14059_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_14472_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_14886_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_7795_15299_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_im

Downsampled 'MareTyrrhenum_8205_8270_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8205_827_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8205_8683_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8205_9097_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8205_9510_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8205_9924_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_820_0_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_820_10337_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_820_10751_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsa

Downsampled 'MareTyrrhenum_8616_413_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_4548_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_4962_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_5375_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_5789_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_6202_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_6616_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_7029_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_8616_7443_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Do

Downsampled 'MareTyrrhenum_9436_17367_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_2067_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_2481_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_2894_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_3308_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_3721_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_4135_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_413_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MareTyrrhenum_9436_4548_0_-30_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
D

#### Tharsis

In [41]:
# size = 2048
name = 'Tharsis'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)

In [37]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Tharsis_000N225E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 225
max_long = 270
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26675, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:19<00:00,  2.16it/s]


In [38]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Tharsis_0_0_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_10337_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_10751_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_11164_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_11578_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_11991_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_12405_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_1240_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_12818_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_0_13232_30_0_270_225.jpg' and saved to 'dataset_generatio

Downsampled 'Tharsis_10257_9097_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10257_9510_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10257_9924_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_0_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_10337_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_10751_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_11164_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_11578_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_11991_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_10667_12405_30_0_270_22

Downsampled 'Tharsis_11078_7443_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_7856_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_8270_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_827_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_8683_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_9097_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_9510_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11078_9924_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11488_0_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11488_10337_30_0_270_225.jpg'

Downsampled 'Tharsis_11898_6616_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_7029_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_7443_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_7856_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_8270_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_827_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_8683_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_9097_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_9510_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_11898_9924_30_0_270_225.jp

...

Downsampled 'Tharsis_6564_2481_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_2894_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_3308_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_3721_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_4135_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_413_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_4548_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_4962_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_5375_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_6564_5789_30_0_270_225.jpg' and sav

Downsampled 'Tharsis_7385_1654_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_16953_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_17367_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_2067_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_2481_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_2894_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_3308_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_3721_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_4135_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_7385_413_30_0_270_225.jpg' and s

Downsampled 'Tharsis_8205_1654_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_16953_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_17367_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_2067_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_2481_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_2894_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_3308_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_3721_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_4135_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8205_413_30_0_270_225.jpg' and s

Downsampled 'Tharsis_8616_14472_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_14886_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_15299_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_15713_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_16126_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_16540_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_1654_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_16953_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_17367_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_8616_2067_30_0_270_225.jpg

Downsampled 'Tharsis_9436_11991_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_12405_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_1240_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_12818_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_13232_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_13645_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_14059_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_14472_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_14886_30_0_270_225.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Tharsis_9436_15299_30_0_270_225.jp

In [415]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

435 200


#### SyrtisMajor

In [14]:
# size = 6144
name = 'Syrtis'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [15]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_SyrtisMajor_00N45E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 45
max_long = 90
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:32<00:00,  1.31it/s]


In [16]:
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800

input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_128052\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Syrtis_0_0_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_11164_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_11578_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_11991_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_12405_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_1240_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_12818_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_0_13232_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downs

Downsampled 'Syrtis_10257_9510_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10257_9924_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_0_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_11164_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_11578_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_11991_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_12405_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_10667_1240_30_0_90_45.jpg' and saved to 'dataset_g

Downsampled 'Syrtis_11077_8683_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11077_9097_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11077_9510_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11077_9924_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_0_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_11164_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_11578_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11487_11991_30_0_90_45.jpg' and saved to 'dataset_ge

Downsampled 'Syrtis_11898_8270_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11898_827_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11898_8683_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11898_9097_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11898_9510_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_11898_9924_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_12308_0_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_12308_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_12308_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_12308_11164_30_0_90_45.jpg' and saved to 'dataset_gener

...

Downsampled 'Syrtis_6974_15299_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_15713_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_16126_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_16540_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_1654_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_16953_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_17367_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_2067_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_2481_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_6974_2894_30_0_90_45.jpg' and saved to 'dataset_generati

Downsampled 'Syrtis_7795_13232_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_13645_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_14059_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_14472_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_14886_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_15299_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_15713_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_16126_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_16540_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_7795_1654_30_0_90_45.jpg' and saved to 'dataset_gener

Downsampled 'Syrtis_820_12405_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_1240_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_12818_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_13232_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_13645_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_14059_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_14472_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_14886_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_15299_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_820_15713_30_0_90_45.jpg' and saved to 'dataset_generation_old/

Downsampled 'Syrtis_9026_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_11164_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_11578_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_11991_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_12405_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_1240_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_12818_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_13232_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9026_13645_30_0_90_45.jpg' and saved to 'dataset_gener

Downsampled 'Syrtis_9436_9510_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9436_9924_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_0_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_10337_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_10751_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_11164_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_11578_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_11991_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_12405_30_0_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Syrtis_9846_1240_30_0_90_45.jpg' and saved to 'dataset_generation_

In [422]:
n = 50
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 50


#### SinusSabaeus

In [44]:
# size = 2048
name = 'SinusSabaeus'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [45]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_SinusSabaeus_30S00E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 0
max_long = 45
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:39<00:00,  1.08it/s]


In [46]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'SinusSabaeus_0_0_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_10337_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_10751_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_11164_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_11578_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_11991_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_12405_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_1240_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_12818_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_0_13232_0_-30_45_0.jpg' a

Downsampled 'SinusSabaeus_10667_0_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_10337_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_10751_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_11164_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_11578_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_11991_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_12405_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_1240_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_10667_12818_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Si

Downsampled 'SinusSabaeus_11077_9097_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11077_9510_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11077_9924_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_0_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_10337_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_10751_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_11164_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_11578_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11487_11991_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Sinu

Downsampled 'SinusSabaeus_11898_7029_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_7443_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_7856_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_8270_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_827_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_8683_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_9097_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_9510_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_11898_9924_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSa

...

Downsampled 'SinusSabaeus_6564_7443_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_7856_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_8270_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_827_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_8683_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_9097_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_9510_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6564_9924_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6974_0_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_6974_1

Downsampled 'SinusSabaeus_7385_5375_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_5789_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_6202_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_6616_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_7029_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_7443_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_7856_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_8270_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_7385_827_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_738

Downsampled 'SinusSabaeus_8205_5375_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_5789_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_6202_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_6616_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_7029_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_7443_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_7856_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_8270_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8205_827_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_820

Downsampled 'SinusSabaeus_8615_2894_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_3308_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_3721_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_4135_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_413_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_4548_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_4962_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_5375_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_8615_5789_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_861

Downsampled 'SinusSabaeus_9436_15713_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_16126_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_16540_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_1654_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_16953_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_17367_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_2067_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_2481_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabaeus_9436_2894_0_-30_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'SinusSabae

In [426]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


#### PhoenicisLacus

In [26]:
# size = 3072
name = 'PhoenicisLacus'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [27]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_PhoenicisLacus_30S225E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 225
max_long = 270
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26675, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:22<00:00,  1.90it/s]


In [28]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_128052\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'PhoenicisLacus_0_0_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_10337_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_10751_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_11164_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_11578_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_11991_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_12405_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_1240_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_0_12818_0_-30_270

Downsampled 'PhoenicisLacus_10257_7856_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_8270_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_827_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_8683_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_9097_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_9510_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10257_9924_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_10667_0_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Phoenic

Downsampled 'PhoenicisLacus_11078_3721_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_4135_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_413_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_4548_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_4962_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_5375_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_5789_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11078_6202_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Phoe

Downsampled 'PhoenicisLacus_11898_15299_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_15713_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_16126_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_16540_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_1654_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_16953_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_17367_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_11898_2067_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsample

...

Downsampled 'PhoenicisLacus_6975_5375_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_5789_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_6202_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_6616_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_7029_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_7443_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_7856_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_6975_8270_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLa

Downsampled 'PhoenicisLacus_7795_1654_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_16953_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_17367_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_2067_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_2481_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_2894_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_3308_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_7795_3721_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Phoenicis

Downsampled 'PhoenicisLacus_820_11578_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_11991_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_12405_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_1240_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_12818_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_13232_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_13645_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_820_14059_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLac

Downsampled 'PhoenicisLacus_8616_5789_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_6202_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_6616_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_7029_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_7443_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_7856_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_8270_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_8616_827_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLac

Downsampled 'PhoenicisLacus_9436_2067_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_2481_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_2894_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_3308_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_3721_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_4135_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_413_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLacus_9436_4548_0_-30_270_225.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'PhoenicisLac

In [430]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

462 200


#### Memnonia

In [29]:

name = 'Memnonia'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name

if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [30]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Memnonia_30S180E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 180
max_long = 225
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:33<00:00,  1.28it/s]


In [31]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/detect_again' # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_128052\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Memnonia_0_0_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_10337_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_10751_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_11164_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_11578_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_11991_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_12405_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_1240_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_0_12818_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detecti

Downsampled 'Memnonia_10257_4962_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_5375_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_5789_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_6202_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_6616_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_7029_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_7443_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_7856_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_10257_8270_0_-30_225_180.jpg' and saved to

Downsampled 'Memnonia_11077_16953_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_17367_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_2067_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_2481_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_2894_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_3308_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_3721_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_4135_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11077_413_0_-30_225_180.jpg' and saved t

Downsampled 'Memnonia_11898_13232_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_13645_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_14059_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_14472_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_14886_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_15299_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_15713_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_16126_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_11898_16540_0_-30_225_180.jpg' and

...

Downsampled 'Memnonia_7385_5789_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_6202_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_6616_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_7029_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_7443_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_7856_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_8270_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_827_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_7385_8683_0_-30_225_180.jpg' and saved to 'dataset_

Downsampled 'Memnonia_8205_2894_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_3308_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_3721_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_4135_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_413_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_4548_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_4962_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_5375_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8205_5789_0_-30_225_180.jpg' and saved to 'dataset_

Downsampled 'Memnonia_8615_14886_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_15299_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_15713_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_16126_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_16540_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_1654_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_16953_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_17367_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_8615_2067_0_-30_225_180.jpg' and saved to '

Downsampled 'Memnonia_9436_11578_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_11991_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_12405_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_1240_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_12818_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_13232_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_13645_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_14059_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9436_14472_0_-30_225_180.jpg' and saved to 

Downsampled 'Memnonia_9846_6616_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_7029_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_7443_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_7856_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_8270_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_827_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_8683_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_9097_0_-30_225_180.jpg' and saved to 'dataset_generation_old/detection_img/detect_again'
Downsampled 'Memnonia_9846_9510_0_-30_225_180.jpg' and saved to 'dataset_

In [434]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

484 200


#### MargaritiferSinus

In [53]:
# size = 2048
name = 'MargaritiferSinus'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name

if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [54]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_MargaritiferSinus_30S315E_100mpp.jpg'
min_lat = -30
max_lat = 0
min_long = -45
max_long = 0
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:19<00:00,  2.23it/s]


In [55]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'MargaritiferSinus_0_0_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_10337_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_10751_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_11164_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_11578_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_11991_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_12405_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_1240_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_0_12818_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/41

Downsampled 'MargaritiferSinus_10257_6202_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_6616_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_7029_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_7443_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_7856_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_8270_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_827_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_8683_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_10257_9097_0_-30_0_-45.jpg' and saved to 'dataset_

Downsampled 'MargaritiferSinus_11077_2481_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_2894_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_3308_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_3721_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_4135_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_413_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_4548_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_4962_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11077_5375_0_-30_0_-45.jpg' and saved to 'dataset_

Downsampled 'MargaritiferSinus_11898_12818_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_13232_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_13645_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_14059_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_14472_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_14886_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_15299_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_15713_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_11898_16126_0_-30_0_-45.jpg' and saved to

...

Downsampled 'MargaritiferSinus_7385_3721_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_4135_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_413_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_4548_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_4962_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_5375_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_5789_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_6202_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_7385_6616_0_-30_0_-45.jpg' and saved to 'dataset_generatio

Downsampled 'MargaritiferSinus_8205_14059_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_14472_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_14886_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_15299_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_15713_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_16126_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_16540_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_1654_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8205_16953_0_-30_0_-45.jpg' and saved to 'dataset_

Downsampled 'MargaritiferSinus_8615_11991_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_12405_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_1240_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_12818_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_13232_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_13645_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_14059_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_14472_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_8615_14886_0_-30_0_-45.jpg' and saved to 'dataset_

Downsampled 'MargaritiferSinus_9436_0_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_10337_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_10751_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_11164_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_11578_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_11991_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_12405_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_1240_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9436_12818_0_-30_0_-45.jpg' and saved to 'dataset_gene

Downsampled 'MargaritiferSinus_9846_4962_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_5375_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_5789_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_6202_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_6616_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_7029_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_7443_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_7856_0_-30_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'MargaritiferSinus_9846_8270_0_-30_0_-45.jpg' and saved to 'dataset_generati

In [438]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

0
0 0


#### LunaePalus

In [56]:
# size = 2048
name = 'LunaePalus'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [57]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_LunaePalus_00N270E_100mpp.jpg'
min_lat = 0
max_lat = 30
min_long = 270
max_long = 315
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:34<00:00,  1.26it/s]


In [58]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'LunaePalus_0_0_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_10337_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_10751_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_11164_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_11578_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_11991_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_12405_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_1240_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_12818_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_0_13232_30_0_315_270.jpg' a

Downsampled 'LunaePalus_10257_9924_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_0_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_10337_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_10751_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_11164_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_11578_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_11991_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_12405_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_10667_1240_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Lun

Downsampled 'LunaePalus_11077_7443_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_7856_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_8270_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_827_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_8683_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_9097_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_9510_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11077_9924_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11487_0_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus

Downsampled 'LunaePalus_11898_4135_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_413_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_4548_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_4962_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_5375_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_5789_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_6202_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_6616_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_11898_7029_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePa

...

Downsampled 'LunaePalus_6564_9924_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_0_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_10337_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_10751_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_11164_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_11578_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_11991_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_12405_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6974_1240_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_6

Downsampled 'LunaePalus_7795_10337_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_10751_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_11164_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_11578_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_11991_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_12405_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_1240_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_12818_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_7795_13232_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePa

Downsampled 'LunaePalus_8205_8270_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8205_827_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8205_8683_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8205_9097_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8205_9510_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8205_9924_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_820_0_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_820_10337_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_820_10751_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_820_11164

Downsampled 'LunaePalus_8615_5789_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_6202_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_6616_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_7029_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_7443_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_7856_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_8270_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_827_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_8683_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_8615_

Downsampled 'LunaePalus_9436_413_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_4548_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_4962_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_5375_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_5789_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_6202_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_6616_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_7029_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_7443_30_0_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'LunaePalus_9436_

In [442]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

479 200


#### Iapygia

In [59]:
# size = 2048
name = 'Iapygia'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [60]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Iapygia_30S45E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 45
max_long = 90
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:52<00:00,  1.23s/it]


In [61]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Iapygia_0_0_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_10337_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_10751_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_11164_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_11578_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_11991_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_12405_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_1240_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_12818_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_0_13232_0_-30_90_45.jpg' and saved to 'dataset_generation_old/dete

Downsampled 'Iapygia_10257_8683_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10257_9097_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10257_9510_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10257_9924_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_0_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_10337_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_10751_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_11164_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_11578_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_10667_11991_0_-30_90_45.jpg' and 

Downsampled 'Iapygia_11077_7029_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_7443_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_7856_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_8270_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_827_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_8683_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_9097_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_9510_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11077_9924_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11487_0_0_-30_90_45.jpg' and saved 

Downsampled 'Iapygia_11898_413_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_4548_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_4962_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_5375_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_5789_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_6202_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_6616_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_7029_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_7443_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_11898_7856_0_-30_90_45.jpg' and sav

...

Downsampled 'Iapygia_6564_14059_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_14472_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_14886_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_15299_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_15713_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_16126_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_16540_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_1654_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_16953_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_6564_17367_0_-30_90_45.jpg' and sav

Downsampled 'Iapygia_7385_13645_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_14059_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_14472_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_14886_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_15299_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_15713_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_16126_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_16540_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_1654_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_7385_16953_0_-30_90_45.jpg' and sav

Downsampled 'Iapygia_8205_11991_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_12405_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_1240_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_12818_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_13232_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_13645_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_14059_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_14472_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_14886_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8205_15299_0_-30_90_45.jpg' and sav

Downsampled 'Iapygia_8615_10337_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_10751_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_11164_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_11578_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_11991_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_12405_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_1240_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_12818_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_13232_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_8615_13645_0_-30_90_45.jpg' and sav

Downsampled 'Iapygia_9436_10751_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_11164_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_11578_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_11991_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_12405_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_1240_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_12818_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_13232_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_13645_0_-30_90_45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Iapygia_9436_14059_0_-30_90_45.jpg' and sav

In [446]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


#### Coprates

In [62]:
# size = 2048
name = 'Coprates'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [63]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Coprates_30S270E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 270
max_long = 315
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:36<00:00,  1.19it/s]


In [64]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Coprates_0_0_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_10337_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_10751_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_11164_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_11578_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_11991_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_12405_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_1240_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_12818_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_0_13232_0_-30_315_270.jpg' and saved t

Downsampled 'Coprates_10257_9510_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10257_9924_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_0_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_10337_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_10751_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_11164_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_11578_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_11991_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_10667_12405_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_106

Downsampled 'Coprates_11077_6202_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_6616_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_7029_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_7443_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_7856_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_8270_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_827_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_8683_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_9097_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11077_9

Downsampled 'Coprates_11898_4962_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_5375_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_5789_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_6202_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_6616_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_7029_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_7443_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_7856_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_8270_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_11898_

...

Downsampled 'Coprates_6974_12818_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_13232_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_13645_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_14059_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_14472_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_14886_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_15299_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_15713_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_16126_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_6974_1

Downsampled 'Coprates_7795_10751_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_11164_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_11578_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_11991_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_12405_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_1240_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_12818_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_13232_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_13645_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_7795_14

Downsampled 'Coprates_8205_827_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8205_8683_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8205_9097_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8205_9510_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8205_9924_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_820_0_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_820_10337_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_820_10751_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_820_11164_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_820_11578_0_-30_315_

Downsampled 'Coprates_8615_7029_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_7443_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_7856_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_8270_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_827_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_8683_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_9097_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_9510_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_8615_9924_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9026_0_0_-30_315

Downsampled 'Coprates_9436_4135_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_413_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_4548_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_4962_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_5375_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_5789_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_6202_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_6616_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_7029_0_-30_315_270.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Coprates_9436_7443_0_-30_

In [450]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

482 200


#### Elysium

In [65]:
# size = 2048
name = 'Elysium'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [66]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Elysium_00N135E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 135
max_long = 180
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:27<00:00,  1.55it/s]


In [67]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Elysium_0_0_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_10337_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_10751_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_11164_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_11578_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_11991_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_12405_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_1240_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_12818_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_0_13232_30_0_180_135.jpg' and saved to 'dataset_generatio

Downsampled 'Elysium_10257_9924_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_0_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_10337_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_10751_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_11164_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_11578_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_11991_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_12405_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_1240_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_10667_12818_30_0_180_1

Downsampled 'Elysium_11077_8270_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11077_827_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11077_8683_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11077_9097_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11077_9510_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11077_9924_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11487_0_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11487_10337_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11487_10751_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11487_11164_30_0_180_135.jp

Downsampled 'Elysium_11898_5789_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_6202_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_6616_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_7029_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_7443_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_7856_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_8270_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_827_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_8683_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_11898_9097_30_0_180_135.jp

...

Downsampled 'Elysium_6564_413_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_4548_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_4962_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_5375_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_5789_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_6202_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_6616_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_7029_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_7443_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_6564_7856_30_0_180_135.jpg' and sav

Downsampled 'Elysium_7385_3721_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_4135_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_413_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_4548_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_4962_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_5375_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_5789_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_6202_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_6616_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_7385_7029_30_0_180_135.jpg' and sav

Downsampled 'Elysium_8205_4135_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_413_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_4548_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_4962_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_5375_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_5789_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_6202_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_6616_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_7029_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8205_7443_30_0_180_135.jpg' and sav

Downsampled 'Elysium_8615_3721_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_4135_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_413_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_4548_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_4962_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_5375_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_5789_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_6202_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_6616_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_8615_7029_30_0_180_135.jpg' and sav

Downsampled 'Elysium_9436_2481_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_2894_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_3308_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_3721_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_4135_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_413_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_4548_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_4962_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_5375_30_0_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Elysium_9436_5789_30_0_180_135.jpg' and sav

In [454]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

469 200


#### Arabia

In [68]:
# size = 2048
name = 'Arabia'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [69]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Arabia_000N000E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 0
max_long = 45
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:49<00:00,  1.14s/it]


In [70]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Arabia_0_0_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_10337_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_10751_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_11164_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_11578_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_11991_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_12405_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_1240_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_12818_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_0_13232_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Ar

Downsampled 'Arabia_10667_1240_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_12818_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_13232_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_13645_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_14059_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_14472_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_14886_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_15299_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_15713_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_10667_16126_30_0_45_0.jpg' and saved to 'dataset_gener

Downsampled 'Arabia_11487_10751_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_11164_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_11578_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_11991_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_12405_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_1240_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_12818_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_13232_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_13645_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11487_14059_30_0_45_0.jpg' and saved to 'dataset_gener

Downsampled 'Arabia_11898_9510_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_11898_9924_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_0_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_10337_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_10751_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_11164_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_11578_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_11991_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_12405_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_12308_1240_30_0_45_0.jpg' and saved to 'dataset_generation_

...

Downsampled 'Arabia_6564_827_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6564_8683_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6564_9097_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6564_9510_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6564_9924_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6974_0_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6974_10337_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6974_10751_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6974_11164_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_6974_11578_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection

Downsampled 'Arabia_7385_827_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7385_8683_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7385_9097_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7385_9510_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7385_9924_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7795_0_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7795_10337_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7795_10751_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7795_11164_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_7795_11578_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection

Downsampled 'Arabia_8205_7029_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_7443_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_7856_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_8270_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_827_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_8683_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_9097_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_9510_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8205_9924_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_820_0_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/

Downsampled 'Arabia_8615_5789_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_6202_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_6616_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_7029_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_7443_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_7856_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_8270_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_827_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_8683_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_8615_9097_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_

Downsampled 'Arabia_9436_4548_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_4962_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_5375_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_5789_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_6202_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_6616_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_7029_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_7443_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_7856_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Arabia_9436_8270_30_0_45_0.jpg' and saved to 'dataset_generation_old/detection

In [458]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


#### Amazonis

In [71]:
# size = 2048
name = 'Amazonis'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [72]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Amazonis_00N180E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 180
max_long = 225
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:19<00:00,  2.26it/s]


In [73]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Amazonis_0_0_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_10337_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_10751_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_11164_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_11578_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_11991_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_12405_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_1240_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_12818_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_0_13232_30_0_225_180.jpg' and saved to 'dataset

Downsampled 'Amazonis_10257_7856_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_8270_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_827_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_8683_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_9097_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_9510_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10257_9924_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10667_0_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10667_10337_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_10667_10751_30_0_2

Downsampled 'Amazonis_11077_7856_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_8270_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_827_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_8683_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_9097_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_9510_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11077_9924_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11487_0_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11487_10337_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11487_10751_30_0_2

Downsampled 'Amazonis_11898_4548_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_4962_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_5375_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_5789_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_6202_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_6616_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_7029_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_7443_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_7856_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_11898_8270_30_0

...

Downsampled 'Amazonis_6974_17367_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_2067_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_2481_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_2894_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_3308_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_3721_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_4135_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_413_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_4548_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_6974_4962_30_0_225_180.j

Downsampled 'Amazonis_7795_16953_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_17367_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_2067_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_2481_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_2894_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_3308_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_3721_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_4135_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_413_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_7795_4548_30_0_225_180.

Downsampled 'Amazonis_820_15299_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_15713_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_16126_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_16540_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_1654_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_16953_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_17367_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_2067_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_2481_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_820_2894_30_0_225_180.jpg' 

Downsampled 'Amazonis_9026_14059_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_14472_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_14886_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_15299_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_15713_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_16126_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_16540_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_1654_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_16953_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9026_17367_30_0_

Downsampled 'Amazonis_9846_14472_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_14886_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_15299_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_15713_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_16126_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_16540_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_1654_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_16953_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_17367_30_0_225_180.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amazonis_9846_2067_30_0_2

In [462]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

418 200


#### Amenthes

In [74]:
# size = 2048
name = 'Amenthes'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [75]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Amenthes_000N090E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = 90
max_long = 135
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26675, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:29<00:00,  1.44it/s]


In [76]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Amenthes_0_0_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_10337_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_10751_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_11164_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_11578_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_11991_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_12405_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_1240_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_12818_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_0_13232_30_0_135_90.jpg' and saved to 'dataset_generatio

Downsampled 'Amenthes_10257_8683_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10257_9097_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10257_9510_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10257_9924_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_0_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_10337_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_10751_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_11164_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_11578_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_10667_11991_30_0_135_90

Downsampled 'Amenthes_11078_5789_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_6202_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_6616_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_7029_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_7443_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_7856_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_8270_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_827_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_8683_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11078_9097_30_0_135_90.jp

Downsampled 'Amenthes_11898_2894_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_3308_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_3721_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_4135_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_413_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_4548_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_4962_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_5375_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_5789_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_11898_6202_30_0_135_90.jp

...

Downsampled 'Amenthes_6564_9924_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_0_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_10337_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_10751_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_11164_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_11578_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_11991_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_12405_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_1240_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_6975_12818_30_0_135_90.jpg' an

Downsampled 'Amenthes_7385_7029_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_7443_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_7856_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_8270_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_827_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_8683_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_9097_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_9510_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7385_9924_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_7795_0_30_0_135_90.jpg' and saved 

Downsampled 'Amenthes_8205_4962_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_5375_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_5789_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_6202_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_6616_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_7029_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_7443_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_7856_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_8270_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8205_827_30_0_135_90.jpg' and sav

Downsampled 'Amenthes_8616_5789_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_6202_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_6616_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_7029_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_7443_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_7856_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_8270_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_827_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_8683_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_8616_9097_30_0_135_90.jpg' and sav

Downsampled 'Amenthes_9436_3308_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_3721_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_4135_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_413_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_4548_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_4962_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_5375_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_5789_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_6202_30_0_135_90.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Amenthes_9436_6616_30_0_135_90.jpg' and sav

In [466]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


#### Aeolis

In [77]:
# size = 2048
name = 'Aeolis'
# pathsave =| 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [78]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_Aeolis_30S135E_100mpp.tif'
min_lat = -30
max_lat = 0
min_long = 135
max_long = 180
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:35<00:00,  1.23it/s]


In [79]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'Aeolis_0_0_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_10337_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_10751_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_11164_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_11578_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_11991_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_12405_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_1240_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_12818_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_0_13232_0_-30_180_135.jpg' and saved to 'dataset_generatio

Downsampled 'Aeolis_10257_9510_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10257_9924_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_0_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_10337_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_10751_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_11164_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_11578_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_11991_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_12405_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_10667_1240_0_-30_180_13

Downsampled 'Aeolis_11077_7443_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_7856_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_8270_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_827_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_8683_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_9097_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_9510_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11077_9924_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11487_0_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11487_10337_0_-30_180_135.jpg'

Downsampled 'Aeolis_11898_6202_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_6616_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_7029_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_7443_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_7856_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_8270_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_827_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_8683_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_9097_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_11898_9510_0_-30_180_135.jp

...

Downsampled 'Aeolis_6974_13232_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_13645_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_14059_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_14472_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_14886_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_15299_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_15713_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_16126_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_16540_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_6974_1654_0_-30_180_135.jp

Downsampled 'Aeolis_7795_13645_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_14059_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_14472_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_14886_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_15299_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_15713_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_16126_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_16540_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_1654_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_7795_16953_0_-30_180_135.jp

Downsampled 'Aeolis_820_11164_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_11578_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_11991_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_12405_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_1240_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_12818_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_13232_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_13645_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_14059_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_820_14472_0_-30_180_135.jpg' and sav

Downsampled 'Aeolis_8615_9510_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_8615_9924_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_0_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_10337_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_10751_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_11164_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_11578_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_11991_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_12405_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9026_1240_0_-30_180_135.jpg' and

Downsampled 'Aeolis_9436_8683_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9436_9097_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9436_9510_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9436_9924_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_0_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_10337_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_10751_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_11164_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_11578_0_-30_180_135.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'Aeolis_9846_11991_0_-30_180_135.jpg' and 

In [470]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

486 200


#### OxiaPalus

In [80]:
# size = 2048
name = 'OxiaPalus'
# pathsave = 'dataset_generation_old/dataset_'+str(size)+'_'+name
pathsave = 'dataset_generation_old/size_variant/dataset_'+str(size)+'_'+name
if os.path.exists(pathsave) == False:
    os.mkdir(pathsave)
    

In [81]:
im_name = 'Themis/THEMIS_DayIR_ControlledMosaic_OxiaPalus_00N315E_100mpp.tif'
min_lat = 0
max_lat = 30
min_long = -45
max_long = 0
generate_data_overlap(max_lat,min_lat,max_long,min_long,pathsave,df,size,im_name,name)

width: 26674, height: 17783, crop size: 416
num in x direction: 64, num in y direction: 42


Parameter format not correct - "size_variant".
Parameter format not correct - "size_variant".
100%|██████████| 43/43 [00:15<00:00,  2.86it/s]


In [82]:
input_folder = pathsave+'/images'
output_folder = 'dataset_generation_old/detection_img/'+str(size) # replace with your output folder path

downsample_images_in_folder(input_folder, output_folder)

C:\Users\jamil\AppData\Local\Temp\ipykernel_16732\685092672.py:8: DeprecationWarning: ANTIALIAS is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.LANCZOS instead.
  resized_img = img.resize(new_size, Image.ANTIALIAS)


Downsampled 'OxiaPalus_0_0_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_10337_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_10751_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_11164_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_11578_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_11991_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_12405_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_1240_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_12818_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_0_13232_30_0_0_-45.jpg' and saved to 'dataset_generatio

Downsampled 'OxiaPalus_10257_7856_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_8270_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_827_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_8683_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_9097_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_9510_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10257_9924_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10667_0_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10667_10337_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_10667_10751_30_0_0_-45.jpg

Downsampled 'OxiaPalus_11077_5375_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_5789_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_6202_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_6616_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_7029_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_7443_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_7856_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_8270_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_827_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11077_8683_30_0_0_-45.jp

Downsampled 'OxiaPalus_11898_5789_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_6202_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_6616_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_7029_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_7443_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_7856_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_8270_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_827_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_8683_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_11898_9097_30_0_0_-45.jp

...

Downsampled 'OxiaPalus_6974_10751_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_11164_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_11578_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_11991_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_12405_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_1240_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_12818_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_13232_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_13645_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_6974_14059_30_0_0_-45.jp

Downsampled 'OxiaPalus_7385_8270_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7385_827_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7385_8683_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7385_9097_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7385_9510_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7385_9924_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7795_0_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7795_10337_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7795_10751_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_7795_11164_30_0_0_-45.jpg' and sav

Downsampled 'OxiaPalus_8205_7443_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_7856_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_8270_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_827_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_8683_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_9097_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_9510_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8205_9924_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_820_0_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_820_10337_30_0_0_-45.jpg' and saved t

Downsampled 'OxiaPalus_8615_4548_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_4962_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_5375_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_5789_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_6202_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_6616_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_7029_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_7443_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_7856_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_8615_8270_30_0_0_-45.jpg' and sa

Downsampled 'OxiaPalus_9436_2067_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_2481_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_2894_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_3308_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_3721_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_4135_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_413_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_4548_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_4962_30_0_0_-45.jpg' and saved to 'dataset_generation_old/detection_img/416'
Downsampled 'OxiaPalus_9436_5375_30_0_0_-45.jpg' and sav

In [474]:
n = 200
path_images = pathsave+'/images'
path_labels = pathsave+'/labels'
files_images = os.listdir(pathsave+'/images') # 800
files_labels = os.listdir(pathsave+'/labels') # 800
random_sample(files_images, files_labels, n)

0
0 0


In [9]:
10838 - 9537

1301

In [12]:
54230*0.13

7049.900000000001

In [8]:
54230*0.14

7592.200000000001

In [23]:
import os
import shutil

# Define the paths to the folders
folder_416 = './dataset_generation_old/detection_img/416'
folder_missing_data = './dataset_generation_old/detection_img/missingdata'

# Ensure the 'missing data' folder exists, create it if not
if not os.path.exists(folder_missing_data):
    os.makedirs(folder_missing_data)

# Search for files containing 'syrtis' in the '416' folder
for filename in os.listdir(folder_416):
    if 'sinussabaeus' in filename.lower():
        file_path = os.path.join(folder_416, filename)
        # Move the file to the 'missing data' folder
        shutil.move(file_path, folder_missing_data)
        print(f"Moved {filename} to 'missing data' folder.")

print("Extraction complete.")


Moved SinusSabaeus_0_0_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_10337_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_10751_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_11164_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_11578_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_11991_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_12405_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_1240_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_12818_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_13232_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_13645_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_14059_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_14472_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_14886_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_0_15299_0_-30_45_0.jpg to 'missing

Moved SinusSabaeus_1230_3308_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_3721_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_4135_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_413_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_4548_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_4962_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_5375_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_5789_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_6202_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_6616_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_7029_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_7443_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_7856_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_1230_8270_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_12

Moved SinusSabaeus_14359_5375_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_5789_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_6202_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_6616_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_7029_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_7443_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_7856_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_8270_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_827_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_8683_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_9097_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_9510_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14359_9924_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_14770_0_0_-30_45_0.jpg to 'missing data' folder.
Moved Sinu

Moved SinusSabaeus_16821_14472_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_14886_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_15299_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_15713_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_16126_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_16540_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_1654_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_16953_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_17367_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_2067_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_2481_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_2894_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_3308_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_16821_3721_0_-30_45_0.jpg to 'missing data' folder

Moved SinusSabaeus_19283_1240_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_12818_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_13232_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_13645_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_14059_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_14472_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_14886_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_15299_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_15713_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_16126_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_16540_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_1654_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_16953_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_19283_17367_0_-30_45_0.jpg to 'missing data' fo

...

Moved SinusSabaeus_22975_7856_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_8270_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_827_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_8683_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_9097_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_9510_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_22975_9924_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_0_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_10337_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_10751_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_11164_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_11578_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_11991_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_23386_12405_0_-30_45_0.jpg to 'missing data' folder.
Move

Moved SinusSabaeus_25437_9097_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25437_9510_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25437_9924_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_0_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_10337_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_10751_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_11164_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_11578_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_11991_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_12405_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_1240_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_12818_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_13232_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_25847_13645_0_-30_45_0.jpg to 'missing data' folder.


Moved SinusSabaeus_4102_4135_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_413_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_4548_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_4962_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_5375_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_5789_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_6202_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_6616_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_7029_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_7443_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_7856_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_8270_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_827_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_4102_8683_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_410

Moved SinusSabaeus_5743_1654_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_16953_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_17367_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_2067_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_2481_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_2894_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_3308_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_3721_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_4135_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_413_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_4548_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_4962_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_5375_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_5743_5789_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_

Moved SinusSabaeus_820_16126_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_16540_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_1654_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_16953_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_17367_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_2067_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_2481_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_2894_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_3308_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_3721_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_4135_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_413_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_4548_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_4962_0_-30_45_0.jpg to 'missing data' folder.
Moved SinusSabaeus_820_5375_0_-

In [18]:
import os
os.getcwd()

'C:\\Users\\jamil\\OneDrive\\desktop\\PhD\\master_fyp'

In [25]:
import os
import shutil

# Define the paths to the folders
folder_416 = './dataset_generation_old/detection_img/416'
folder_missing_data = './dataset_generation_old/detection_img/detectagain'

# Ensure the 'missing data' folder exists, create it if not
if not os.path.exists(folder_missing_data):
    os.makedirs(folder_missing_data)

# Search for files containing 'syrtis' in the '416' folder
for filename in os.listdir(folder_416):
    if 'memnonia' in filename.lower():
        file_path = os.path.join(folder_416, filename)
        # Copy the file to the 'missing data' folder
        shutil.copy(file_path, folder_missing_data)
        print(f"Copied {filename} to 'missing data' folder.")

print("Extraction complete.")


Copied Memnonia_0_0_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_10337_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_10751_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_11164_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_11578_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_11991_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_12405_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_0_15299_0_-30_225_180.jpg to 'missing

Copied Memnonia_11077_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_16953_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11077_17367_0_-30_225_180.jpg to 'missing data' fo

Copied Memnonia_11898_9097_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11898_9510_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_11898_9924_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_0_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_10337_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_10751_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_11164_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_11578_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_11991_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_12405_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12308_13645_0_-30_225_180.jpg to 'missing data' folder.


Copied Memnonia_12718_4962_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_5375_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_5789_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_6202_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_6616_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_7029_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_7443_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_7856_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_8270_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_827_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_8683_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_9097_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_9510_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_12718_9924_0_-30_225_180.jpg to 'missing data' folder.
Copied 

Copied Memnonia_13949_2067_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_2481_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_2894_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_3308_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_3721_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_4135_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_413_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_4548_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_4962_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_5375_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_5789_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_6202_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_6616_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_13949_7029_0_-30_225_180.jpg to 'missing data' folder.
Copied 

...

Copied Memnonia_5333_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_16953_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_5333_17367_0_-30_225_180.jpg to 'missing data' folder.
Copied M

Copied Memnonia_6564_11991_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_12405_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_6564_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied M

Copied Memnonia_7795_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_16953_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_17367_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_2067_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_7795_2481_0_-30_225_180.jpg to 'missing data' folder.
Copied Me

Copied Memnonia_8615_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_16953_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_17367_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_2067_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_2481_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_8615_2894_0_-30_225_180.jpg to 'missing data' folder.
Copied Mem

Copied Memnonia_9846_12405_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_1240_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_12818_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_13232_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_13645_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_14059_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_14472_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_14886_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_15299_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_15713_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_16126_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_16540_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_1654_0_-30_225_180.jpg to 'missing data' folder.
Copied Memnonia_9846_16953_0_-30_225_180.jpg to 'missing data' folder.
Copied M